# Assignment 2

### Problem 1: Speech Denoising Using Deep Learning 

1. If you took my MLSP class, you may think that you’ve seen this problem. But, it’s actually somewhat different from what you did before, so read carefully. And, this time you SHOULD implement a DNN with at least two hidden layers. So, don’t reuse your legacy MATLAB code for this problem.

2. When you attended IUB, you took a course taught by Prof. K. Since you really liked his lectures, you decided to record them without the professor’s permission. You felt awkward, but you did it anyway because you really wanted to review his lectures later.

3. Although you meant to review the lecture every time, it turned out that you never listened to it. After graduation, you realized that a lot of concepts you face at work were actually covered by Prof. K’s class. So, you decided to revisit the lectures and study the materials once again using the recordings.

4. You should have reviewed your recordings earlier. It turned out that a fellow student who used to sit next to you always ate chips in the middle of the class right beside your microphone. So, Prof. K’s beautiful deep voice was contaminated by the annoying chip eating noise.

5. But, you vaguly recall that you learned some things about speech denoising and source sep- aration from Prof. K’s class. So, you decided to build a simple deep learning-based speech denoiser that takes a noisy speech spectrum (speech plus chip eating noise) and then produces a cleaned-up speech spectrum.

6. Since you don’t have Prof. K’s clean speech signal, I prepared this male speech data recorded by other people. train dirty male.wav and
train clean male.wav are the noisy speech and its corresponding clean speech you are going to use for training the network. Take a listen to them. Load them and covert them into spectrograms, which are the matrix representation of signals. 


### Loading Libraries

In [14]:
import numpy as np
import tensorflow as tf
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from matplotlib.pyplot import imshow
import keras
from keras.models import Sequential
from keras.layers.core import Dense, Activation
from keras.models import Model
from tensorflow.keras import layers
import librosa
import IPython.display as ipd


In [2]:
from google.colab import drive
drive.mount('/content/drive') 

Mounted at /content/drive


### Loading the data and performing stft

In [ ]:
   #!pip install librosa # in colab, you’ll need to install this
   import librosa
   
   s, sr=librosa.load('/content/drive/MyDrive/Deep Learning Assignment/train_clean_male.wav', sr=None)
   S=librosa.stft(s, n_fft=1024, hop_length=512)
   sn, sr=librosa.load('/content/drive/MyDrive/Deep Learning Assignment/train_dirty_male.wav', sr=None)
   X=librosa.stft(sn, n_fft=1024, hop_length=512)


7. Take their magnitudes by using np.abs() or whatever suitable method, because S and X are complex valued. Let’s call them |S| and |X|.

In [ ]:
S_abs = np.abs(S).T
X_abs = np.abs(X).T

8. Train a fully-connected deep neural network. A couple of hidden layers would work, but feel free to try out whatever structure, activation function, initialization scheme you’d like. The input to the network is a column vector of |X| (a 513-dim vector) and the target is its corresponding one in |S|. You may want to do some mini-batching for this. Make use of whatever functions in Tensorflow or Pytorch.
9. But, remember that your network should predict nonnegative magnitudes as output. Try to use a proper activation function in the last layer to make sure of that. I don’t care which activation function you use in the middle layers.

#### Model Architechture

In [ ]:

#define the keras model
model = Sequential()
He_initializer = tf.keras.initializers.HeNormal()
model.add(Dense(512, input_dim = 513, activation='relu',kernel_initializer=He_initializer))
model.add(Dense(512, activation='relu', kernel_initializer=He_initializer))
model.add(Dense(512, activation='relu', kernel_initializer=He_initializer))
model.add(Dense(513, activation='relu', kernel_initializer=He_initializer))

model.compile(optimizer='adam',loss='mse')


In [ ]:
model.summary()

Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_4 (Dense)              (None, 512)               263168    
_________________________________________________________________
dense_5 (Dense)              (None, 512)               262656    
_________________________________________________________________
dense_6 (Dense)              (None, 512)               262656    
_________________________________________________________________
dense_7 (Dense)              (None, 513)               263169    
Total params: 1,051,649
Trainable params: 1,051,649
Non-trainable params: 0
_________________________________________________________________


#### Training the model

In [ ]:
model.fit(x = X_abs, y = S_abs,epochs=100, batch_size=10,shuffle=True,verbose=2)

Epoch 1/100
246/246 - 1s - loss: 0.0076
Epoch 2/100
246/246 - 1s - loss: 0.0080
Epoch 3/100
246/246 - 1s - loss: 0.0065
Epoch 4/100
246/246 - 1s - loss: 0.0067
Epoch 5/100
246/246 - 1s - loss: 0.0065
Epoch 6/100
246/246 - 1s - loss: 0.0074
Epoch 7/100
246/246 - 1s - loss: 0.0072
Epoch 8/100
246/246 - 1s - loss: 0.0058
Epoch 9/100
246/246 - 1s - loss: 0.0057
Epoch 10/100
246/246 - 1s - loss: 0.0062
Epoch 11/100
246/246 - 1s - loss: 0.0064
Epoch 12/100
246/246 - 1s - loss: 0.0057
Epoch 13/100
246/246 - 1s - loss: 0.0056
Epoch 14/100
246/246 - 1s - loss: 0.0057
Epoch 15/100
246/246 - 1s - loss: 0.0054
Epoch 16/100
246/246 - 1s - loss: 0.0055
Epoch 17/100
246/246 - 1s - loss: 0.0052
Epoch 18/100
246/246 - 1s - loss: 0.0053
Epoch 19/100
246/246 - 1s - loss: 0.0061
Epoch 20/100
246/246 - 1s - loss: 0.0054
Epoch 21/100
246/246 - 1s - loss: 0.0057
Epoch 22/100
246/246 - 1s - loss: 0.0050
Epoch 23/100
246/246 - 1s - loss: 0.0050
Epoch 24/100
246/246 - 1s - loss: 0.0050
Epoch 25/100
246/246 - 1s

10. test 01 x.wav is the test noisy signal. Load them and apply STFT as before. Feed the mag- nitude spectra of this test mixture |Xtest| to your network and predict their clean magnitude spectra |Sˆtest|. Then, you can recover the (complex-valued) speech spectrogram of the test signal in this way:


$ \widehat{S} = \frac{X_{test}}{|X_{test}|}\odot \widehat{|S_{test}|} $

which means you take the phase information of the input noisy signal Xtest and use that to |X test |
recover the clean speech. ⊙ stands for the Hadamard product and the division is element-wise, too.

11. Recover the time domain speech signal by applying an inverse-STFT on Sˆtest, which will give you a vector. Let’s call this cleaned-up test speech signal sˆtest. I’ll calculate something called Signal-to-Noise Ratio (SNR) by comparing it with the ground truth speech I didn’t share with you. It should be reasonably good. You can actually write it out by using the following code:


#### Test file 1 (test 01 x.wav)

In [ ]:
test_x_01, sr=librosa.load('/content/drive/MyDrive/Deep Learning Assignment/test_x_01.wav', sr=None)
test_x_01_stft =librosa.stft(test_x_01, n_fft=1024, hop_length=512)
test_x_01_abs = np.abs(test_x_01_stft).T


#### Predicting on the test data

In [ ]:
S_test_x_01 = model.predict(test_x_01_abs)


#### Recovering the signal by doing inverse stft

In [ ]:
S_hat_test_x_01 = np.multiply(test_x_01_stft/test_x_01_abs.T,S_test_x_01.T)
S_istft = librosa.istft(S_hat_test_x_01, hop_length=512)

#### Recovered signal removing noise

In [2]:
import IPython.display as ipd
ipd.Audio(S_istft, rate = sr)

In [ ]:
import soundfile as sf
sf.write('test_s_01_recons.wav', S_istft, sr)


12. Do the same testing procedure for test 02 x.wav, which actually contains Prof. K’s voice along with the chip eating noise. Enjoy his enhanced voice using your DNN.

#### Test file 2 (test 02 x.wav)

In [ ]:
test_x_02, sr=librosa.load('/content/drive/MyDrive/Deep Learning Assignment/test_x_02.wav', sr=None)
test_x_02_stft =librosa.stft(test_x_02, n_fft=1024, hop_length=512)
test_x_02_abs = np.abs(test_x_02_stft).T


#### Predicting on the test data

In [ ]:
S_test_x_02 = model.predict(test_x_02_abs)

In [ ]:
S_hat_test_x_02 = np.multiply(test_x_02_stft/test_x_02_abs.T,S_test_x_02.T)
S_istft = librosa.istft(S_hat_test_x_02, hop_length=512)

In [ ]:
import soundfile as sf
sf.write('test_s_02_recons.wav', S_istft, sr)

#### Recovered signal

In [3]:
import IPython.display as ipd
ipd.Audio(S_istft, rate = sr)

### Problem 2: Speech Denoising Using 1D CNN

1. As an audio guy it’s sad to admit, but a lot of audio signal processing problems can be solved in the time-frequency domain, or an image version of the audio signal. You’ve learned how to do it in the previous homework by using STFT and its inverse process.

2. What that means is nothing stops you from applying a CNN to the same speech denoising problem. In this question, I’m asking you to implement a 1D CNN that does the speech denoising job in the STFT magnitude domain. 1D CNN here means a variant of CNN which does the convolution operation along only one of the axes. In our case it’s the frequency axis.

3. Like you did in homework 1 Q2, install/load librosa. Take the magnitude spectrograms of the dirty signal and the clean signal |X| and |S|.

4. Both in Tensorflow and PyTorch, you’d better transpose this matrix, so that each row of the matrix is a spectrum. Your 1D CNN will take one of these row vectors as an example, i.e. |X|⊤:,i. Since this is not an RGB image with three channels, nor you’ll use any other information than just the magnitude during training, your input image has only one channel (depth-wise). Coupled with your choice of the minibatch size, the dimensionality of your minibatch would be like this: [(batch size) × (number of channels) × (height) × (width)] = [B × 1 × 1 × 513]. Note that depending on the implementation of the 1D CNN layers in TF or PT, it’s okay to omit the height information. Carefully read the definition of the function you’ll use.

5. You’ll also need to define the size of the kernel, which will be 1 × D, or simply D depending on the implementation (because we know that there’s no convolution along the height axis).


6. If you define K kernels in the first layer, the output feature map’s dimension will be [B × K × 1 × (513 − D + 1)]. You don’t need too many kernels, but feel free to investigate. You don’t need too many hidden layers, either.

7. In the end, you know, you have to produce an output matrix of [B × 513], which are the approximation of the clean magnitude spectra of the batch. It’s a dimension hard to match using CNN only, unless you take care of the edges by padding zeros (let’s not do zero-padding for this homework). Hence, you may want to flatten the last feature map as a vector, and add a regular linear layer to reduce that dimensionality down to 513.


8. Meanwhile, although this flattening-followed-by-linear-layer approach should work in theory, the dimensionality of your flattened CNN feature map might be too large. To handle this issue, we will used the concept we learned in class, striding: usually, a stride larger than 1 can reduce the dimensionality after each CNN layer. You could consider this option in all convolutional layers to reduce the size of the feature maps gradually, so that the input dimensionality of the last fully-connected (FC) layer is manageable. Maxpooling, coupled with the striding technique, would be something to consider.


9. Be very careful about this dimensionality, because you have to define the input and output dimensionality of the FC layer in advance. For example, a stride of 2 pixels will reduce the feature dimension down to roughly 50%, though not exactly if the original dimensionality is an odd number.


10. Don’t forget to apply the activation function of your choice, at every layer, especially in the last layer.


11. Try whatever optimization techniques you’ve learned so far.


12. Check on the quality of the test signals you used in P1. Here, once again, you have no good way to judge the quality of the test results other than listening to them.




#### Loading the data and doing stft

In [ ]:
s, sr=librosa.load('/content/drive/MyDrive/Deep Learning Assignment/train_clean_male.wav', sr=None)
S=librosa.stft(s, n_fft=1024, hop_length=512)
sn, sr=librosa.load('/content/drive/MyDrive/Deep Learning Assignment/train_dirty_male.wav', sr=None)
X=librosa.stft(sn, n_fft=1024, hop_length=512)

#### Taking absolute value and reshaping 

In [ ]:
S_abs = np.abs(S).T
X_abs = np.abs(X).T

S_abs = S_abs.reshape(2459,513,1)
X_abs = X_abs.reshape(2459,513,1)

In [ ]:

X_abs.shape,S_abs.shape

((2459, 513, 1), (2459, 513, 1))

#### Model Architechture

In [ ]:
from tensorflow.keras.layers import Conv1D
from tensorflow.keras.layers import MaxPooling1D
from tensorflow.keras.layers import Flatten

model = Sequential()
model.add(Conv1D(filters=64, kernel_size=3, activation='relu',input_shape=(513,1)))
model.add(MaxPooling1D(pool_size=2))
model.add(Conv1D(filters=64, kernel_size=3, activation='relu'))
model.add(MaxPooling1D(pool_size=2))
model.add(Flatten())
model.add(Dense(1024, activation='relu'))
model.add(Dense(513, activation='relu'))

model.compile(optimizer='adam',loss='mse')

print(model.summary())

Model: "sequential_4"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv1d_6 (Conv1D)            (None, 511, 64)           256       
_________________________________________________________________
max_pooling1d_6 (MaxPooling1 (None, 255, 64)           0         
_________________________________________________________________
conv1d_7 (Conv1D)            (None, 253, 64)           12352     
_________________________________________________________________
max_pooling1d_7 (MaxPooling1 (None, 126, 64)           0         
_________________________________________________________________
flatten_2 (Flatten)          (None, 8064)              0         
_________________________________________________________________
dense_8 (Dense)              (None, 1024)              8258560   
_________________________________________________________________
dense_9 (Dense)              (None, 513)              

#### Fitting the model

In [ ]:
model.fit(x = X_abs, y = S_abs,epochs=100, batch_size=128)

Epoch 1/100
20/20 [==============================] - 28s 40ms/step - loss: 0.0571
Epoch 2/100
20/20 [==============================] - 0s 18ms/step - loss: 0.0260
Epoch 3/100
20/20 [==============================] - 0s 17ms/step - loss: 0.0160
Epoch 4/100
20/20 [==============================] - 0s 17ms/step - loss: 0.0120
Epoch 5/100
20/20 [==============================] - 0s 17ms/step - loss: 0.0099
Epoch 6/100
20/20 [==============================] - 0s 17ms/step - loss: 0.0085
Epoch 7/100
20/20 [==============================] - 0s 17ms/step - loss: 0.0076
Epoch 8/100
20/20 [==============================] - 0s 17ms/step - loss: 0.0068
Epoch 9/100
20/20 [==============================] - 0s 17ms/step - loss: 0.0062
Epoch 10/100
20/20 [==============================] - 0s 18ms/step - loss: 0.0058
Epoch 11/100
20/20 [==============================] - 0s 17ms/step - loss: 0.0055
Epoch 12/100
20/20 [==============================] - 0s 16ms/step - loss: 0.0052
Epoch 13/100
20/20 [====

#### Test file 1 (test 01 x.wav)

In [ ]:
test_x_01, sr=librosa.load('/content/drive/MyDrive/Deep Learning Assignment/test_x_01.wav', sr=None)
test_x_01_stft =librosa.stft(test_x_01, n_fft=1024, hop_length=512)
test_x_01_abs = np.abs(test_x_01_stft).T

#### Reshaping the test output and doing prediction

In [ ]:
test_x_01_abs_reshape = test_x_01_abs.reshape(142,513,1)
S_test_x_01 = model.predict(test_x_01_abs_reshape)

In [ ]:
## Checking the shapes
print("predcition shape",S_test_x_01.shape)
print("stft shape", test_x_01_stft.shape)
print("stft absolute shape",test_x_01_abs.shape )

predcition shape (142, 513)
stft shape (513, 142)
stft absolute shape (142, 513)


#### Extracting the recovered signal

In [ ]:
S_hat_test_x_01 = np.multiply(test_x_01_stft/test_x_01_abs.T,S_test_x_01.T)
S_istft = librosa.istft(S_hat_test_x_01, hop_length=512)

#### Recovered signal

In [4]:
ipd.display(ipd.Audio(S_istft,rate=sr,embed=True))

In [ ]:
import soundfile as sf
sf.write('test_s_01_recons_cnn1D.wav', S_istft, sr)

#### Test file 2 (test 02 x.wav)

In [ ]:
test_x_02, sr=librosa.load('/content/drive/MyDrive/Deep Learning Assignment/test_x_02.wav', sr=None)
test_x_02_stft =librosa.stft(test_x_02, n_fft=1024, hop_length=512)
test_x_02_abs = np.abs(test_x_02_stft).T

#### Reshaping the test output and doing prediction

In [ ]:
test_x_02_abs_reshape = test_x_02_abs.reshape(380,513,1)
S_test_x_02 = model.predict(test_x_02_abs_reshape)

In [ ]:
## Checking the shapes
print("predcition shape",S_test_x_02.shape)
print("stft shape", test_x_02_stft.shape)
print("stft absolute shape",test_x_02_abs.shape )

predcition shape (380, 513)
stft shape (513, 380)
stft absolute shape (380, 513)


#### Extracting the recovered signal

In [ ]:
S_hat_test_x_01 = np.multiply(test_x_02_stft/test_x_02_abs.T,S_test_x_02.T)
S_istft = librosa.istft(S_hat_test_x_02, hop_length=512)

#### Recovered Signal

In [5]:
ipd.display(ipd.Audio(S_istft,rate=sr,embed=True))

In [ ]:
import soundfile as sf
sf.write('test_s_02_recons_cnn1D.wav', S_istft, sr)

### Problem 3: Speech Denoising Using 2D CNN

1. Now that we know the audio source separation problem can be solved in the image represen- tation, nothing stops us from using 2D CNN for this.

2. To this end, let’s define our input “image” properly. You extract an image of 20 × 513 out of the entire STFT magnitude spectrogram (transposed). That’s an input sample. Using this your 2D CNN estimates the cleaned-up spectrum that corresponds to the last (20th) input frame:
into account to predict the clean spectrum of the current frame, t + 19.

3. Your next image will be another 20 frames shifted by one frame:
|S⊤:,t+20| ≈ FCNN􏰀|X⊤:,t+1:t+20|􏰁, (4)
and so on. Therefore, a pair of adjacent images (unless you shuffle the order) will be with 19 overlapped frames. Since your original STFT spectrogram has 2,459 frames, you can create 2,440 such images as your training dataset.

4. Therefore the input to the 2D CNN will be of [(batch size) ×1 × 20 × 513].

5. Your 2D CNN should be of course with a kernel whose size along both the width (frequencies)
and the height axes (frames) should be larger than 1. Feel free to investigate different sizes.

6. Otherwise, the basic idea must be similar with the 1D CNN case. You’ll still need those techniques as well as the FC layer.

7. Report the denoising results in the same way. One thing to note is that your output will be with only 2,440 spectra, and it’s lacking the first 19 frames. You can ignore those first few frames when you calculate the SNR of the training results. A better way is to augment your input X with 19 silent frames (some magnitude spectra with very small random numbers) in the beginning to match the dimension. I recommend the latter approach.

In [8]:
import librosa
s, sr=librosa.load('/content/drive/MyDrive/Deep Learning Assignment/train_clean_male.wav', sr=None)
S=librosa.stft(s, n_fft=1024, hop_length=512)
sn, sr=librosa.load('/content/drive/MyDrive/Deep Learning Assignment/train_dirty_male.wav', sr=None)
X=librosa.stft(sn, n_fft=1024, hop_length=512)

#### Creating a 3D matrix for training 

In [9]:
X_abs=np.abs(X).T
S_abs=np.abs(S).T

window=20
l=0

train_3d =X_abs[:window,:]
l=1

while l<=X_abs.shape[0]-window:
  train_3d=np.append(train_3d,X_abs[l:l+window,:],axis=0)
  l+=1

train_3d=train_3d.reshape((2440,20,513,1))
y_train=S_abs[:2440,:]
y_train=y_train.reshape((2440,513,1))


#### Model architechture

In [10]:
from tensorflow.keras.layers import Conv2D
from tensorflow.keras.layers import MaxPooling2D
from tensorflow.keras.layers import Flatten
from tensorflow.keras.layers import Input

model = Sequential()
model.add(Input(shape = (20,513,1)))
model.add(Conv2D(100, kernel_size=(7,7), activation='relu', strides = 1))
model.add(MaxPooling2D(pool_size=(2, 2), strides=2, padding="valid"))
model.add(Conv2D(50, kernel_size=(5,5), activation='relu',strides = 1))
model.add(MaxPooling2D(pool_size=(2, 2), strides=2, padding="valid"))
model.add(Flatten())
model.add(Dense(513, activation='relu',kernel_initializer = tf.keras.initializers.HeNormal()))

print(model.summary())


model.compile(optimizer=tf.keras.optimizers.Adam(learning_rate=0.001),loss='mse')

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv2d (Conv2D)              (None, 14, 507, 100)      5000      
_________________________________________________________________
max_pooling2d (MaxPooling2D) (None, 7, 253, 100)       0         
_________________________________________________________________
conv2d_1 (Conv2D)            (None, 3, 249, 50)        125050    
_________________________________________________________________
max_pooling2d_1 (MaxPooling2 (None, 1, 124, 50)        0         
_________________________________________________________________
flatten (Flatten)            (None, 6200)              0         
_________________________________________________________________
dense (Dense)                (None, 513)               3181113   
Total params: 3,311,163
Trainable params: 3,311,163
Non-trainable params: 0
______________________________________________

#### Fitting the model

In [11]:
model.fit(x=train_3d,y=y_train,batch_size=32,epochs=100,shuffle=True,verbose=2)

Epoch 1/100
77/77 - 33s - loss: 0.0754
Epoch 2/100
77/77 - 3s - loss: 0.0581
Epoch 3/100
77/77 - 2s - loss: 0.0430
Epoch 4/100
77/77 - 2s - loss: 0.0350
Epoch 5/100
77/77 - 2s - loss: 0.0291
Epoch 6/100
77/77 - 3s - loss: 0.0252
Epoch 7/100
77/77 - 2s - loss: 0.0230
Epoch 8/100
77/77 - 3s - loss: 0.0213
Epoch 9/100
77/77 - 3s - loss: 0.0203
Epoch 10/100
77/77 - 2s - loss: 0.0187
Epoch 11/100
77/77 - 3s - loss: 0.0180
Epoch 12/100
77/77 - 3s - loss: 0.0177
Epoch 13/100
77/77 - 3s - loss: 0.0168
Epoch 14/100
77/77 - 3s - loss: 0.0152
Epoch 15/100
77/77 - 3s - loss: 0.0156
Epoch 16/100
77/77 - 3s - loss: 0.0150
Epoch 17/100
77/77 - 2s - loss: 0.0143
Epoch 18/100
77/77 - 2s - loss: 0.0134
Epoch 19/100
77/77 - 2s - loss: 0.0158
Epoch 20/100
77/77 - 2s - loss: 0.0140
Epoch 21/100
77/77 - 2s - loss: 0.0137
Epoch 22/100
77/77 - 3s - loss: 0.0136
Epoch 23/100
77/77 - 3s - loss: 0.0130
Epoch 24/100
77/77 - 2s - loss: 0.0125
Epoch 25/100
77/77 - 3s - loss: 0.0116
Epoch 26/100
77/77 - 3s - loss: 0

#### Prediction on train data

In [12]:
predictions=model.predict(train_3d,batch_size=32,verbose=0)

X=X[:,:2440]
mag=(X/np.abs(X))
recovered_signal=mag*predictions.T
recovered_signal=librosa.istft(recovered_signal,hop_length=512)

In [10]:
ipd.Audio(recovered_signal, rate=sr)

#### Prediction on Test file 1 (test 01 x.wav)

In [16]:
test_x_01, sr=librosa.load('/content/drive/MyDrive/Deep Learning Assignment/test_x_01.wav', sr=None)
test_x_01_stft =librosa.stft(test_x_01, n_fft=1024, hop_length=512)
test_x_01_abs = np.abs(test_x_01_stft).T

#### Creating 3d matrix for Test file 1

In [17]:
window=20
l=0

x_test_1 =test_x_01_abs[:window,:]
l=1

while l<=test_x_01_abs.shape[0]-window:
  x_test_1=np.append(x_test_1,test_x_01_abs[l:l+window,:],axis=0)
  l+=1

x_test_1=x_test_1.reshape((123,20,513,1))

#### Prediction

In [29]:
predictions=model.predict(x_test_1,batch_size=32,verbose=0)

test_x_01_stft=test_x_01_stft[:,:123]
mag=(test_x_01_stft/np.abs(test_x_01_stft))

recovered_signal=mag*predictions.T
recovered_signal=librosa.istft(recovered_signal,hop_length=512)

#### Recovered

In [9]:
ipd.Audio(recovered_signal, rate=sr)

In [30]:
import soundfile as sf
sf.write('/content/drive/MyDrive/Deep Learning Assignment/test_s_01_recons_cnn2.wav', recovered_signal, sr)

#### Prediction on Test file 2 (test 02 x.wav)

In [20]:
test_x_02, sr=librosa.load('/content/drive/MyDrive/Deep Learning Assignment/test_x_02.wav', sr=None)
test_x_02_stft =librosa.stft(test_x_02, n_fft=1024, hop_length=512)
test_x_02_abs = np.abs(test_x_02_stft).T

#### Creating 3 D matrix for test file 2

In [21]:
window=20
l=0

x_test_2 =test_x_02_abs[:window,:]
l=1

while l<=test_x_02_abs.shape[0]-window:
  x_test_2=np.append(x_test_2,test_x_02_abs[l:l+window,:],axis=0)
  l+=1

x_test_2=x_test_2.reshape((361,20,513,1))

#### Prediction on test file 2

In [24]:
predictions=model.predict(x_test_2,batch_size=32,verbose=0)

test_x_02_stft=test_x_02_stft[:,:361]
mag=(test_x_02_stft/np.abs(test_x_02_stft))

recovered_signal=mag*predictions.T
recovered_signal=librosa.istft(recovered_signal,hop_length=512)

#### Recovered signal

In [12]:
ipd.Audio(recovered_signal, rate=sr)

In [28]:
import soundfile as sf
sf.write('/content/drive/MyDrive/Deep Learning Assignment/test_s_02_recons_cnn2.wav', recovered_signal, sr)